# Correlation of Cascadia magnetic susceptibility logs using dynamic time warping

Supplementary material to the manuscript "Turbidite correlation for paleoseismology" by Nieminski et al.

Requirements
* numpy
* matplotlib
* pandas
* librosa
* scipy
* tqdm

In [1]:
import numpy as np
import matplotlib.pyplot as plt
import pandas as pd
import random
from librosa.sequence import dtw
from scipy import stats

# set up graphics:
%matplotlib qt
plt.rcParams['svg.fonttype'] = 'none'

## Functions used in the analysis

In [2]:
def normalize_log(log, **kwargs):
    """
    normalize logs
    if the optional parameters 'minlog' and 'maxlog' are provided, they will be used in the normalization
    if they are not provided, the 1st and 99th percentiles of the log will be used as minimum and maximum values
    """
    if len(kwargs) == 0: # if 'minlog' and 'maxlog' are not defined
        minlog = np.nanpercentile(log[log != -999.25], 1)
        maxlog = np.nanpercentile(log[log != -999.25], 99)
    else:
        minlog = kwargs['minlog']
        maxlog = kwargs['maxlog']
    if minlog != maxlog:
        log_n = (log - minlog)/(maxlog - minlog) # calculate normalized GR curve
        log_n[log_n > 1] = 1.0 # clipping
        log_n[log_n < 0] = 0.0 # clipping
    else:
        log_n = log
    return log_n

def correlate_logs(log1, log2, exponent):
    """
    correlate logs, using dynamic time warping
    """
    r = len(log1)
    c = len(log2)
    sm = np.zeros((r,c)) # similarity matrix
    for i in range(0,r):
        sm[i,:] = (np.abs(log2 - log1[i]))**exponent
    D, wp = dtw(C = sm) # dynamic time warping
    p = wp[:,0] # correlation indices for first curve
    q = wp[:,1] # correlation indices for second curve
    p = np.array(p)
    q = np.array(q)
    return p, q, D

def get_yl_br_color(log_value):
    """
    get color from the yellow-brown spectrum for a certain log value
    """
    color = np.array([1-0.4*log_value, 1-0.7*log_value, 0.6-0.6*log_value])
    color[color > 1] = 1
    color[color < 0] = 0
    return color

def plot_correlation(log1, log2, d1, d2, p, q, step):
    """
    plot correlation between two logs
    """
    # for correlation at the sample scale
    fig = plt.figure(figsize=(6,20))
    ax = fig.add_subplot(111)
    ax.plot(log1, d1 - np.min(d1), 'b', linewidth=1) # we want units of d1 and d2
    ax.plot(log2 + 2, d2 - np.min(d2), 'b', linewidth=1)
    ax.plot([1, 1],[0, np.max(d1-np.min(d1))], 'k', linewidth=0.5)
    ax.plot([2, 2],[0, np.max(d2-np.min(d2))], 'k', linewidth=0.5)
    ax.set_xlim(0, 3)
    ax.set_ylim(0, max(np.max(d1-np.min(d1)), np.max(d2-np.min(d2))))
    log1 = 1 - log1
    log2 = 1 - log2
    min_d = min(np.min(d1),np.min(d2))
    max_d = max(np.max(d1),np.max(d2))
#     ax.text(0.1, 0 - (max_d-min_d)*0.01, well1.name)
#     ax.text(2.1, 0 - (max_d-min_d)*0.01, well2.name)
    for i in range(0, len(p)-step, step):
        # intervals for log on the left:
        depth1_base = d1[p[i]]-np.min(d1)
        depth1_top = d1[p[i+step]]-np.min(d1)
        if p[i+step] < p[i]:
            mean_log1 = np.mean(log1[p[i+step]: p[i]])
            x = [0, 1, 1, 0]
            y = [depth1_base, depth1_base, depth1_top, depth1_top]
            ax.fill(x, y, facecolor=get_yl_br_color(mean_log1), edgecolor=None)
        else:
            mean_log1 = log1[p[i]]
        # intervals for log on the right:
        depth2_base = d2[q[i]]-np.min(d2)
        depth2_top = d2[q[i+step]]-np.min(d2)
        if q[i+step] < q[i]:  
            mean_log2 = np.mean(log2[q[i+step]: q[i]])
            x = [2, 3, 3, 2]
            y = [depth2_base, depth2_base, depth2_top, depth2_top]
            ax.fill(x, y, facecolor=get_yl_br_color(mean_log2), edgecolor=None)
        else:
            mean_log2 = log2[q[i]]
        # intervals between the two logs:
        if (p[i+step] < p[i]) or (q[i+step] < q[i]):
            mean_logs = (mean_log1 + mean_log2)*0.5
            x = [1, 2, 2, 1]
            y = [depth1_base, depth2_base, depth2_top, depth1_top]
            plt.fill(x, y, facecolor=get_yl_br_color(mean_logs), edgecolor=None)
    depth1_base = d1[p[i+step]]-np.min(d1) # last layer, log on left
    depth1_top = d1[p[-1]]-np.min(d1)
    if p[-1] < p[i+step]:
        mean_log1 = np.mean(log1[p[-1] : p[i+step]])
        x = [0, 1, 1, 0]
        y = [depth1_base, depth1_base, depth1_top, depth1_top]
        plt.fill(x, y, facecolor=get_yl_br_color(mean_log1), edgecolor=None)
    else:
        mean_log1 = log1[p[i+step]]
    depth2_base = d2[q[i+step]]-np.min(d2) # last layer, log on right
    depth2_top = d2[q[-1]]-np.min(d2)
    if q[-1] < q[i+step]:  
        mean_log2 = np.mean(log2[q[-1] : q[i+step]])
        x = [2, 3, 3, 2]
        y = [depth2_base, depth2_base, depth2_top, depth2_top]
        plt.fill(x, y, facecolor=get_yl_br_color(mean_log2), edgecolor=None)
    else:
        mean_log2 = log2[q[i+step]]
    # intervals between the two logs (last layer):
    if (p[-1] < p[i+step]) or (q[-1] < q[i+step]):
        mean_logs = (mean_log1 + mean_log2)*0.5
        x = [1, 2, 2, 1]
        y = [depth1_base, depth2_base, depth2_top, depth1_top]
        plt.fill(x, y, facecolor=get_yl_br_color(mean_logs), edgecolor=None)
    ax.set_xticks([])
    ax.invert_yaxis()
    labels = []
    start_depth = np.ceil(np.min(d1)/100) * 100
    end_depth = np.floor(np.max(d1)/100) * 100
    for label in np.arange(start_depth, end_depth+1, 100):
        labels.append(str(label))
    ax.set_yticks(np.arange(start_depth, end_depth+1, 100) - np.min(d1))
    ax.set_yticklabels(labels)
    ax.set_ylabel('depth (cm)', fontsize=12)
    ax2 = ax.twinx()
    labels = []
    start_depth = np.ceil(np.min(d2)/100) * 100
    end_depth = np.floor(np.max(d2)/100) * 100
    for label in np.arange(start_depth, end_depth+1, 100):
        labels.append(str(label))
    ax2.set_yticks(np.arange(start_depth, end_depth+1, 100) - np.min(d2))
    ax2.set_yticklabels(labels)
    ax2.set_ylim(0, max(np.max(d1-np.min(d1)), np.max(d2-np.min(d2))))
    ax2.invert_yaxis()
    
    
def correlate_and_plot_logs(log1, log2, d1, d2, exponent):
    """
    correlate two logs using DTW and plot the results; also compute correlation coefficient
    """
    p, q, D = correlate_logs(log1, log2, exponent = exponent) 
    plot_correlation(log1, log2, d1, d2, p, q, step=1)
    vsh_means1 = log1[p]
    vsh_means1[np.where(np.diff(p)==0)[0] + 1] = np.nan
    vsh_means2 = log2[q]
    vsh_means2[np.where(np.diff(q)==0)[0] + 1] = np.nan
    slope, intercept, r_value, p_value, slope_std_error = stats.linregress(vsh_means1[(np.isnan(vsh_means1)==0) & (np.isnan(vsh_means2)==0)], 
                                                                          vsh_means2[(np.isnan(vsh_means1)==0) & (np.isnan(vsh_means2)==0)])
    return slope, intercept, r_value, p_value, slope_std_error

## Load data

In [3]:
df = pd.read_csv('/Users/zoltan/Dropbox/Cascadia_USGS/_____22data/all_log_data/M990722PC.csv')
ms_22 = np.array(df['MS'])
md_22 = np.array(df['DEPTH'])

df = pd.read_csv('/Users/zoltan/Dropbox/Cascadia_USGS/_____22data/all_log_data/M990723PC.csv')
ms_23 = np.array(df['MS'])
md_23 = np.array(df['DEPTH'])

df = pd.read_csv('/Users/zoltan/Dropbox/Cascadia_USGS/_____22data/all_log_data/M990725PC.csv')
ms_25 = np.array(df['MS'])
md_25 = np.array(df['DEPTH'])

df = pd.read_csv('/Users/zoltan/Dropbox/Cascadia_USGS/_____22data/all_log_data/M990712PC.csv')
ms_12 = np.array(df['MS'])
md_12 = np.array(df['DEPTH'])

df = pd.read_csv('/Users/zoltan/Dropbox/Cascadia_USGS/_____22data/all_log_data/M990711PC.csv')
ms_11 = np.array(df['MS'])
md_11 = np.array(df['DEPTH'])

df = pd.read_csv('/Users/zoltan/Dropbox/Cascadia_USGS/_____22data/all_log_data/M990714TC.csv')
ms_14 = np.array(df['MS'])
md_14 = np.array(df['DEPTH'])

df = pd.read_csv('/Users/zoltan/Dropbox/Cascadia_USGS/_____22data/all_log_data/RR56PC.csv')
ms_56 = np.array(df['MS'])
md_56 = np.array(df['DEPTH'])

df = pd.read_csv('/Users/zoltan/Dropbox/Cascadia_USGS/_____22data/all_log_data/RR02PC.csv')
ms_02 = np.array(df['MS'])
md_02 = np.array(df['DEPTH'])

df = pd.read_csv('/Users/zoltan/Dropbox/Cascadia_USGS/_____22data/all_log_data/M990730PC.csv')
ms_30 = np.array(df['MS'])
md_30 = np.array(df['DEPTH'])

df = pd.read_csv('/Users/zoltan/Dropbox/Cascadia_USGS/_____22data/all_log_data/M990731PC.csv')
ms_31 = np.array(df['MS'])
md_31 = np.array(df['DEPTH'])

df = pd.read_csv('/Users/zoltan/Dropbox/Cascadia_USGS/_____22data/all_log_data/M990709TC.csv')
ms_09 = np.array(df['MS'])
md_09 = np.array(df['DEPTH'])

## 22-23 correlation

In [4]:
# results depend a lot on how exactly the normalization is done!
slope, intercept, r_value, p_value, slope_std_error = correlate_and_plot_logs(normalize_log(ms_22), 
                                                    normalize_log(ms_23)[95:], md_22, md_23[95:], exponent = 0.3)

In [5]:
r_value

0.7342660093725707

In [6]:
p_value

5.577791501337756e-72

In [7]:
r_values_dict = {}
r_values_dict['22-23'] = 0.7342660093725705

## 23-25 correlation

In [8]:
slope, intercept, r_value, p_value, slope_std_error = correlate_and_plot_logs(normalize_log(ms_23), 
                                                    normalize_log(ms_25[:670]), md_23, md_25[:670], exponent=0.3)

In [9]:
r_value

0.3341421258649587

In [10]:
p_value

8.059952008946789e-15

In [11]:
r_values_dict['23-25'] = 0.3341421258649592

## 25-22 correlation

In [13]:
slope, intercept, r_value, p_value, slope_std_error = correlate_and_plot_logs(normalize_log(ms_25[:670])[85:], 
                                                    normalize_log(ms_22), md_25[85:670], md_22, exponent=0.3)

In [14]:
r_value

0.5395722728219895

In [15]:
p_value

4.425935864348273e-34

In [16]:
r_values_dict['25-22'] = 0.5395722728219894

## 23-12 correlation

In [17]:
slope, intercept, r_value, p_value, slope_std_error = correlate_and_plot_logs(normalize_log(ms_23), 
                                                    normalize_log(ms_12[:236]), md_23, md_12[:236], exponent = 0.3)

In [18]:
r_value

0.32159782401297804

In [19]:
p_value

8.279661540839753e-07

In [20]:
r_values_dict['23-12'] = 0.32159782401297804

## 12-11 correlation

In [21]:
slope, intercept, r_value, p_value, slope_std_error = correlate_and_plot_logs(normalize_log(ms_12), 
                                                    normalize_log(ms_11), md_12, md_11, exponent = 0.3)

In [22]:
r_value

0.37181786305217285

In [23]:
p_value

1.1678534344007381e-14

In [24]:
r_values_dict['12-11'] = 0.3718178630521732

#### This is the Goldfinger et al. correlation (between T6 and T20):

In [26]:
slope, intercept, r_value, p_value, slope_std_error = correlate_and_plot_logs(normalize_log(ms_12)[77:321], 
                                            normalize_log(ms_11)[:211], md_12[77:321], md_11[:211], exponent = 0.3)

In [27]:
r_value

0.41455717974773026

#### Correlation of a restricted interval (with better looking correlation than the previous two):

In [28]:
slope, intercept, r_value, p_value, slope_std_error = correlate_and_plot_logs(normalize_log(ms_12)[157:359], 
                                            normalize_log(ms_11)[156:334], md_12[157:359], md_11[156:334], exponent = 0.3)

In [29]:
r_value

0.5331745074920322

## 23-14 correlations

In [30]:
slope, intercept, r_value, p_value, slope_std_error = correlate_and_plot_logs(normalize_log(ms_23)[:592], 
                                                    normalize_log(ms_14)[:590], md_23[:592], md_14[:590], exponent = 0.3)

In [31]:
r_value

0.5955173123299082

In [32]:
p_value

2.4852991527884303e-19

In [33]:
r_values_dict['23-14'] = r_value

## 56-31 correlation

Hydrate Ridge Basin West - Rogue Canyon

If you take away T19 at the bottom of 56, the correlation looks worse (and the correlation coefficient is smaller).

In [34]:
slope, intercept, r_value, p_value, slope_std_error = correlate_and_plot_logs(normalize_log(ms_56)[55:], 
                                                normalize_log(ms_31[:587]), md_56[55:], md_31[:587], exponent = 0.3)

In [14]:
slope, intercept, r_value, p_value, slope_std_error = correlate_and_plot_logs(normalize_log(ms_56), 
                                                normalize_log(ms_31[:587]), md_56, md_31[:587], exponent = 0.3)

In [35]:
r_value

0.6707145161779475

In [36]:
p_value

3.5268791548414903e-71

In [37]:
r_values_dict['56-31'] = 0.6707145161779474

## 30-31 correlation
Rogue Canyon

In [39]:
# the 30 log needs a lot of fixing; this way it matches Figure 33 in Goldfinger et al. 2012 
md_30 = np.hstack((md_30[:615], md_30[715:]))
ms_30 = np.hstack((ms_30[:615], ms_30[715:]))
inds = np.where((md_30 > 400) & (md_30 < 500))[0]
ms_30[inds] = ms_30[inds[::-1]]

In [40]:
slope, intercept, r_value, p_value, slope_std_error = correlate_and_plot_logs(normalize_log(ms_30[:747]), 
                                            normalize_log(ms_31[27:]), md_30[:747], md_31[27:], exponent = 0.3)

In [41]:
r_value

0.7510565372785213

In [42]:
p_value

1.7304912171837393e-104

In [43]:
r_values_dict['30-31'] = r_value

## Randomization

### Create 'database' of individual turbidites

In [44]:
def onclick_boundary(event, xs, fig):
    """function for collecting depth values for a stratigraphic top from a chronostratigraphic diagram

    :param event: mouse click event
    :param xs: x coordinates of points clicked in cross section
    :param ys: y coordinates (depth values) of points clicked in cross section
    :param fig: figure handle of cross section"""
    x1 = event.xdata
    xs.append(x1)
    ax = fig.axes[0]
    xlim = ax.get_xlim()
    ylim = ax.get_ylim()
    ax.plot([x1, x1], [-30, 600], 'r')
    fig.canvas.draw_idle()
    ax.set_xlim(xlim)
    ax.set_ylim(ylim)
    
def create_figure_for_clicking(md, log, miny, maxy):
    fig = plt.figure(figsize=(18,3))
    plt.plot(md, log)
    plt.ylim(miny, maxy)
    plt.xlim(md[0], md[-1])
    plt.xlabel('depth(cm)')
    return fig

In [234]:
# code for manually interpreting turbidite tops (see collected data below)
fig = create_figure_for_clicking(md_31, ms_31, -30, 600)
xs = []
cid = fig.canvas.mpl_connect('button_press_event', lambda event: onclick_boundary(event, xs, fig))

In [238]:
# xs = [0] + xs
# tops_31 = xs
tops_31

[0,
 17.430107526881727,
 39.88458781362007,
 65.62508960573479,
 113.82007168458782,
 143.941935483871,
 174.0637992831541,
 210.75770609318997,
 250.1899641577061,
 286.33620071684595,
 354.247311827957,
 394.77491039426525,
 441.8745519713261,
 481.3068100358423,
 522.3820788530466,
 555.24229390681,
 573.863082437276,
 595.2222222222222,
 641.226523297491,
 664.2286738351255,
 680.6587813620072,
 700.3749103942653]

In [45]:
tops_22 = [0.0, 13.040143369175638, 43.848745519713276, 91.6551971326165, 129.19211469534054, 
           175.5820788530466, 231.53333333333336, 273.673835125448, 307.31541218637994, 
           367.5161290322581, 403.28243727598567, 439.4028673835126, 486.50107526881726]

tops_23 = [7.784946236559151, 30.40143369175628, 73.37275985663082, 112.27311827956989, 
           155.69677419354838, 209.97634408602153, 261.089605734767, 318.9878136200717, 
           376.88602150537633, 426.64229390681, 463.28100358422944, 492.68243727598565, 
           518.0129032258064, 533.8444444444444, 559.6272401433691, 587.6716845878136, 
           618.8824372759857, 632]

tops_25 = [0, 47.103225806451604, 111.98924731182797, 171.752688172043, 240.05376344086022, 
           308.92401433691754, 380.64014336917563, 427.8817204301076, 476.8308243727599, 
           506.9971326164875, 529.7641577060931, 559.9304659498207, 615.7096774193549, 
           662.9512544802867, 684.5799283154122, 706.7777777777778, 743.2050179211469, 
           780.7706093189963]

tops_56 = [0, 80.721146953405, 104.02795698924729, 176.2222222222222, 218.2881720430107, 
           302.4200716845878, 333.6853046594981, 435.43942652329747, 525.2559139784946, 
           567.3218637992832, 609.9562724014337, 643.495340501792, 655.4329749103943, 
           664.5283154121863, 685.5612903225806, 724.2164874551971, 781.6308243727598]

tops_30 = [0, 15.574193548387086, 44.419354838709666, 96.4537634408602, 129.82365591397848, 
           163.19354838709677, 206.74408602150538, 243.50752688172042, 288.18924731182796, 
           341.92043010752684, 376.9870967741935, 431.8494623655914, 462.95698924731175, 
           478.79354838709673, 537.6150537634409, 574.3784946236559, 594.174193548387, 
           616.2322580645161, 639.421505376344, 667.1354838709677]

tops_31 = [0, 17.430107526881727, 39.88458781362007, 65.62508960573479, 113.82007168458782, 
           143.941935483871, 174.0637992831541, 210.75770609318997, 250.1899641577061, 
           286.33620071684595, 354.247311827957, 394.77491039426525, 441.8745519713261, 
           481.3068100358423, 522.3820788530466, 555.24229390681, 573.863082437276, 
           595.2222222222222, 641.226523297491, 664.2286738351255, 680.6587813620072, 700.3749103942653]

In [46]:
turb_logs = []
depth_logs = []
log_number = []

def add_turbidites_to_database(turb_logs, depth_logs, log_number, log, md, tops):
    count = 0
    for i in range(len(tops) - 1):
        turb_logs.append(log[(md < tops[i+1]) & (md >= tops[i])])
        depth_log = md[(md < tops[i+1]) & (md >= tops[i])]
        depth_log = depth_log - min(depth_log)
        depth_logs.append(depth_log)
        log_number.append(count)
        count += 1

add_turbidites_to_database(turb_logs, depth_logs, log_number, ms_22, md_22, tops_22)
add_turbidites_to_database(turb_logs, depth_logs, log_number, ms_23, md_23, tops_23)
add_turbidites_to_database(turb_logs, depth_logs, log_number, ms_25, md_25, tops_25)
add_turbidites_to_database(turb_logs, depth_logs, log_number, ms_56, md_56, tops_56)
add_turbidites_to_database(turb_logs, depth_logs, log_number, ms_30, md_30, tops_30)
add_turbidites_to_database(turb_logs, depth_logs, log_number, ms_31, md_31, tops_31)

In [47]:
len(depth_logs)

102

In [48]:
def plot_logs_w_turb_boundaries(md, log, tops):
    fig = plt.figure()
    plt.plot(md, normalize_log(log), '.-')
    plt.ylim(0, 1)
    count = 0
    for i in range(len(tops)):
        plt.plot([tops[i], tops[i]], [0, 1], 'r' )
        plt.text(tops[i], 0.2, str(count))
        count += 1
    return fig

In [80]:
# check how the tops look like when plotted on the log
fig = plot_logs_w_turb_boundaries(md_23, ms_23, tops_23)

In [57]:
from tqdm import trange

def correlate_log_w_synthetic_logs(md, log, thickness, nit, exponent, turb_logs, depth_logs):
    r_values = []
    for i in trange(nit):
        exponent = exponent
        log1 = normalize_log(log)
        d1 = md
        fake_log = np.array([])
        md_log = np.array([])
        max_depth = 0
        while max_depth <= thickness:
            ind = random.choices(np.arange(len(turb_logs)), k=1)[0]
            fake_log = np.hstack((fake_log, turb_logs[ind].flatten()))
            if len(md_log) == 0:
                md_log = np.hstack((md_log, 1 + depth_logs[ind]))
            else:
                md_log = np.hstack((md_log, 1 + md_log[-1] + depth_logs[ind]))
            max_depth = md_log[-1]
        log2 = normalize_log(fake_log)
        d2 = md_log
        p, q, D = correlate_logs(log1, log2, exponent)
        vsh_means1 = log1[p]
        vsh_means1[np.where(np.diff(p)==0)[0] + 1] = np.nan
        vsh_means2 = log2[q]
        vsh_means2[np.where(np.diff(q)==0)[0] + 1] = np.nan
        slope, intercept, r_value, p_value, slope_std_rror = stats.linregress(vsh_means1[(np.isnan(vsh_means1)==0) & (np.isnan(vsh_means2)==0)], 
                                                                          vsh_means2[(np.isnan(vsh_means1)==0) & (np.isnan(vsh_means2)==0)])
        r_values.append(r_value)
        step = 1
        if r_value > 0.85:
            plot_correlation(log1, log2, d1, d2, p, q, step)
            print(r_value)
    return r_values

def correlate_synth_log_w_synth_logs(thickness, nit, exponent, turb_logs, depth_logs):
    """
    correlate synthetic log pairs
    """
    r_values = []
    for i in trange(nit):
        # create first log:
        fake_log = np.array([])
        md_log = np.array([])
        max_depth = 0
        inds = []
        while max_depth <= thickness:
            ind = random.choices(np.arange(len(turb_logs)), k=1)[0]
            inds.append(ind)
            fake_log = np.hstack((fake_log, turb_logs[ind].flatten()))
            if len(md_log) == 0:
                md_log = np.hstack((md_log, 1 + depth_logs[ind]))
            else:
                md_log = np.hstack((md_log, 1 + md_log[-1] + depth_logs[ind]))
            max_depth = md_log[-1]
        log1 = normalize_log(fake_log)
        d1 = md_log.copy()
        
        # create second log:
        fake_log = np.array([])
        md_log = np.array([])
        max_depth = 0
        while max_depth <= thickness:
            ind = random.choices(np.arange(len(turb_logs)), k=1)[0]
            if ind not in inds: # make sure that we are not using any of the turbidites in the first log
                fake_log = np.hstack((fake_log, turb_logs[ind].flatten()))
                if len(md_log) == 0:
                    md_log = np.hstack((md_log, 1 + depth_logs[ind]))
                else:
                    md_log = np.hstack((md_log, 1 + md_log[-1] + depth_logs[ind]))
                max_depth = md_log[-1]
        log2 = normalize_log(fake_log)
        d2 = md_log.copy()
        
        p, q, D = correlate_logs(log1, log2, exponent)
        vsh_means1 = log1[p]
        vsh_means1[np.where(np.diff(p)==0)[0] + 1] = np.nan
        vsh_means2 = log2[q]
        vsh_means2[np.where(np.diff(q)==0)[0] + 1] = np.nan
        slope, intercept, r_value, p_value, slope_std_rror = \
            stats.linregress(vsh_means1[(np.isnan(vsh_means1)==0) \
            & (np.isnan(vsh_means2)==0)], vsh_means2[(np.isnan(vsh_means1)==0) & (np.isnan(vsh_means2)==0)])
        r_values.append(r_value)
        step = 1
        if r_value > 0.85: # plot correlation if r value is very large
            plot_correlation(log1, log2, d1, d2, p, q, step)
            print(r_value)
    return r_values


In [142]:
r_values = correlate_log_w_synthetic_logs(md_14, ms_14, np.max(md_14), 10000, 0.3, turb_logs, depth_logs)

793

In [58]:
# compute r values for 10000 synthetic log pairs (this is better than correlating actual logs with synthetic logs)
r_values = correlate_synth_log_w_synth_logs(700, 10000, 0.3, turb_logs, depth_logs)

100%|███████████████████████████████████████████████████████████████████████████████████████████████████| 10000/10000 [01:45<00:00, 94.49it/s]


In [60]:
df = pd.DataFrame(r_values_dict, index = ['r values'])

In [61]:
len(turb_logs) # 90 turbidites

102

In [62]:
# create datafrme of r values of core correlations
df = pd.DataFrame(r_values_dict, index = ['r values'])

In [63]:
df

22-23     23-25     25-22     23-12     12-11     23-14  \
r values  0.734266  0.334142  0.539572  0.321598  0.371818  0.595517   

             56-31     30-31  
r values  0.670715  0.751057

In [64]:
df2 = pd.read_csv('/Users/zoltan/Dropbox/Cascadia_USGS/_____22data/all_log_data/___well_list_all_UTM.csv')
df2.head()

Unnamed: 0   wellname        x (m)        y (m)  top (cm)  base (cm)  \
0           0  M990701PC  323155.4523  5094231.965       3.0      217.0   
1           1  M990702TC  322976.8965  5092876.617       3.0      153.0   
2           2  M990703PC  323444.5234  5093790.767       3.0      348.0   
3           3  M990705TC  248942.3983  5280304.395       1.0      230.0   
4           4  M990709TC  223659.7642  5349668.355       1.0      249.0   

   kb elevation (m)  
0                 0  
1                 0  
2                 0  
3                 0  
4                 0

In [65]:
df2['x (m)'][df2['wellname'] == 'M990723PC'].values[0]

164836.4388

In [66]:
def compute_dist(wname1, wname2, df):
    # compute distnace between two cores
    x1 = df['x (m)'][df['wellname'] == wname1].values[0]
    y1 = df['y (m)'][df['wellname'] == wname1].values[0]
    x2 = df['x (m)'][df['wellname'] == wname2].values[0]
    y2 = df['y (m)'][df['wellname'] == wname2].values[0]
    dist = ((x2 - x1)**2 + (y2 - y1)**2)**0.5
    return dist

compute_dist('M990722PC', 'M990723PC', df2)

4.262547567105501

In [67]:
# lists of core names for correlated core pairs
wnames1 = ['M990722PC', 'M990723PC', 'M990725PC', 'M990723PC', 'M990712PC', 'M990723PC', 'RR56PC', 'M990730PC']
wnames2 = ['M990723PC', 'M990725PC', 'M990722PC', 'M990712PC', 'M990711PC', 'M990714TC', 'M990731PC', 'M990731PC']

In [68]:
# distances between core pairs
dists = {}
for wname1, wname2, colname in zip(wnames1, wnames2, df.columns):
    dists[colname] = compute_dist(wname1, wname2, df2)
dists

{'22-23': 4.262547567105501,
 '23-25': 9511.690019966634,
 '25-22': 9515.952274584322,
 '23-12': 303287.693331802,
 '12-11': 11.700880736187145,
 '23-14': 252323.17211422455,
 '56-31': 248306.88838134793,
 '30-31': 1882.0695570917978}

In [69]:
# dataframe of distances
df3 = pd.DataFrame(dists, index = ['distance (m)'])
df3

22-23       23-25        25-22          23-12      12-11  \
distance (m)  4.262548  9511.69002  9515.952275  303287.693332  11.700881   

                      23-14          56-31        30-31  
distance (m)  252323.172114  248306.888381  1882.069557

In [70]:
# add distances to dataframe of r values
df = df.append(df3)
df

/var/folders/5h/h0hb76hj7h90xczzdv1425fr0000gp/T/ipykernel_69219/2505547045.py:1: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(df3)


22-23        23-25        25-22          23-12      12-11  \
r values      0.734266     0.334142     0.539572       0.321598   0.371818   
distance (m)  4.262548  9511.690020  9515.952275  303287.693332  11.700881   

                      23-14          56-31        30-31  
r values           0.595517       0.670715     0.751057  
distance (m)  252323.172114  248306.888381  1882.069557

In [71]:
# comoute p values
r_values = np.array(r_values)
p_values = {}
for colname, r_value in zip(df.columns, df.iloc[0]):
    p_values[colname] = len(r_values[r_values > r_value])/10000

In [160]:
df2 = pd.DataFrame(p_values, index = ['p values'])
df2

22-23  23-25  25-22  23-12   12-11   23-14   56-31   30-31
p values  0.0066  0.928  0.387  0.939  0.8758  0.1994  0.0511  0.0043

In [161]:
# add p values to dataframe
df = df.append(df2)
df

22-23        23-25        25-22          23-12      12-11  \
r values      0.734266     0.334142     0.539572       0.321598   0.371818   
distance (m)  4.262548  9511.690020  9515.952275  303287.693332  11.700881   
p values      0.006600     0.928000     0.387000       0.939000   0.875800   

                      23-14          56-31        30-31  
r values           0.595517       0.670715     0.744543  
distance (m)  252323.172114  248306.888381  1882.069557  
p values           0.199400       0.051100     0.004300

In [162]:
# final version of dataframe
df = df.transpose()
df

r values   distance (m)  p values
22-23  0.734266       4.262548    0.0066
23-25  0.334142    9511.690020    0.9280
25-22  0.539572    9515.952275    0.3870
23-12  0.321598  303287.693332    0.9390
12-11  0.371818      11.700881    0.8758
23-14  0.595517  252323.172114    0.1994
56-31  0.670715  248306.888381    0.0511
30-31  0.744543    1882.069557    0.0043

In [76]:
plt.figure()
plt.hist(r_values, 50)
cmap = plt.get_cmap("tab10")
for r_value in df['r values']:
    plt.plot([r_value, r_value], [0, 570], color=cmap(1), linewidth = 2)
plt.xlim(0, 0.9)
plt.ylim(0, 570);

In [409]:
df.to_csv('p_values_of_correlations.csv')

In [77]:
plt.figure()
plt.scatter(df['distance (m)'], df['p values'])
plt.plot([-10000, 320000], [0.05, 0.05], '--', color=cmap(1))
plt.xlim(-10000, 320000)
plt.xlabel('distance (m)')
plt.ylabel('p value');